In [2]:
import numpy as np
import pandas as pd
import automatminer as amm
import pymatgen as mg
import glob
from itertools import zip_longest
from matminer.data_retrieval.retrieve_MP import MPDataRetrieval
from sklearn.model_selection import KFold
from sys import getsizeof
from tqdm import tqdm
from matminer.featurizers.structure import GlobalInstabilityIndex

In [3]:
def generate_labels_from_structures():
    """Creates a DataFrame with labels based on structure files."""
    counter = 0
    data = {}
    for filename in glob.glob("../Structures/Metals/*.cif"):
        struct = mg.Structure.from_file(filename)
        formula = struct.composition.reduced_formula
        filepath = filename.split('Structures/')[-1]
        data[counter] = {'composition': formula, 'Label': 0, 'structure': struct}
        counter+=1
    
    for filename in glob.glob("../Structures/Insulators/*.cif"):
        struct = mg.Structure.from_file(filename)
        formula = struct.composition.reduced_formula
        filepath = filename.split('Structures/')[-1]
        data[counter] = {'composition': formula, 'Label': 0, 'structure': struct}
        counter+=1 
    
    for filename in glob.glob("../Structures/MIT_materials/*/*.cif"):
        struct = mg.Structure.from_file(filename)
        formula = struct.composition.reduced_formula
        filepath = filename.split('Structures/')[-1]
        data[counter] = {'composition': formula, 'Label': 1, 'structure': struct}
        counter+=1
    
    df = pd.DataFrame.from_dict(data, orient='index')
    return df

In [4]:
df = generate_labels_from_structures()
df.head()

/home/nicholas/miniconda3/envs/dev/lib/python3.7/site-packages/pymatgen/io/cif.py:1101: UserWarning:

Issues encountered while parsing CIF: Some fractional co-ordinates rounded to ideal values to avoid finite precision errors.



composition  Label                                          structure
0      W18O49      0  [[15.37975385  1.893       6.78296238] W5+, [ ...
1      CaCrO3      0  [[2.58311502 2.83194208 1.872325  ] Ca2+, [0.0...
2         TiO      0  [[0. 0. 0.] Ti2+, [3.38051503e-16 2.10215000e+...
3    SrLaNiO4      0  [[0.      0.      7.92112] Sr2+:0.500, La3+:0....
4     Sr2RuO4      0  [[0.         0.         8.24768178] Sr2+, [0. ...

In [5]:
prod_config = amm.presets.get_preset_config("express")
pipe = amm.pipeline.MatPipe(**prod_config)

In [ ]:
prod_config

In [ ]:
prod_config['reducer'].reducers = ('tree',)
prod_config['reducer'].reducers

In [ ]:
prod_config['autofeaturizer'].featurizers['structure'].append(GlobalInstabilityIndex())

In [ ]:
prod_config['learner'].tpot_kwargs

In [ ]:
prod_config['learner'].tpot_kwargs['max_time_mins'] = 15
# prod_config['learner'].tpot_kwargs['warm_start'] = True
# prod_config['learner'].tpot_kwargs['max_eval_time_mins'] = 10

In [ ]:
skfold = KFold(n_splits=5, random_state=1) #We will use a 5-Fold object.
#predicted_folds = pipe.benchmark(df, "Label", skfold)

In [ ]:
pipe.fit(df, "Label")

In [ ]:
pipe.save("mat.pipe")

In [9]:
pipe = amm.pipeline.MatPipe.load("mat.pipe")

2019-07-15 10:44:36 INFO     Loaded MatPipe from file mat.pipe.
2019-07-15 10:44:36 WARNING  Only use this model to make predictions (do not retrain!). Backend was serialzed as only the top model, not the full automl backend. 


In [10]:
def create_subdataframe(chunk):
    subdf = pd.DataFrame(chunk, columns=['filepath'])
    subdf['structure'] = subdf['filepath'].apply(mg.core.structure.Structure.from_file)
    subdf.index = subdf['filepath'].str.split("/").str[-1].str.strip('.cif').str.split("_").str[-1]
    subdf['composition'] = subdf['structure'].apply(lambda x: x.composition)
    subdf.drop(columns='filepath', inplace=True)
    predictions = pipe.predict(subdf, 'Label')
    predictions['probability'] = pipe.learner.backend.predict_proba(
        predictions.drop(columns=['Label predicted']))[:,1]
    return predictions

In [11]:
files = glob.glob("/home/nicholas/Desktop/band_gap_model_cifs/*.cif")
# masterdf = create_subdataframe(files[0:2])
dflist = []
n = 500
chunks = [files[i * n:(i + 1) * n] for i in range((len(files) + n - 1) // n )]
for chunk in chunks:
    subdf = create_subdataframe(chunk)
    dflist.append(subdf)
masterdf = pd.concat(dflist)
masterdf

2019-07-15 10:44:54 INFO     Beginning MatPipe prediction using fitted pipeline.
2019-07-15 10:44:54 INFO     AutoFeaturizer: Starting transforming.
2019-07-15 10:44:54 INFO     AutoFeaturizer: composition column already exists, overwriting with composition from structure.



2019-07-15 10:44:55 INFO     AutoFeaturizer: Guessing oxidation states of compositions, as they were not present in input.



2019-07-15 10:44:55 INFO     AutoFeaturizer: Featurizing with AtomicOrbitals.


/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/composition.py:416: UserWarning:

AtomicOrbitals: Na+7 Ti3+7 Ti4+6 O2-26 truncated to Na7Ti13O26

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/composition.py:416: UserWarning:

AtomicOrbitals: Li+8 Co3+4 Co4+6 Ni2+2 O2-24 truncated to Li4Co5NiO12

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/composition.py:416: UserWarning:

AtomicOrbitals: Ti4+3 Mn2+3 Mn3+12 P5+18 O2-72 truncated to TiMn5(PO4)6

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/composition.py:416: UserWarning:

AtomicOrbitals: Li+6 Mn3+2 Mn4+2 O2-10 truncated to Li3Mn2O5

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/composition.py:416: UserWarning:

AtomicOrbitals: Mn2+1 Mn3+5 O2-5 F-


2019-07-15 10:44:55 INFO     AutoFeaturizer: Featurizing with ElementProperty.


...

2019-07-15 15:58:58 INFO     AutoFeaturizer: Featurizing with SineCoulombMatrix.


/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part

/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part



/home/nicholas/Dropbox/Rondinelli_Research/Metal-insulator Transitions/src/matminer/matminer/featurizers/structure.py:743: ComplexWarning:

Casting complex values to real discards the imaginary part



2019-07-15 15:59:10 INFO     AutoFeaturizer: Featurizer type bandstructure not in the dataframe. Skipping...
2019-07-15 15:59:10 INFO     AutoFeaturizer: Featurizer type dos not in the dataframe. Skipping...
2019-07-15 15:59:10 INFO     AutoFeaturizer: Finished transforming.
2019-07-15 15:59:10 INFO     DataCleaner: Starting transforming.
2019-07-15 15:59:10 INFO     DataCleaner: Cleaning with respect to samples with sample na_method 'fill'
2019-07-15 15:59:10 INFO     DataCleaner: Replacing infinite values with nan for easier screening.
2019-07-15 15:59:11 INFO     DataCleaner: One-hot encoding used for columns ['HOMO_character', 'HOMO_element', 'LUMO_character', 'LUMO_element', 'crystal_system']
2019-07-15 15:59:11 INFO     DataCleaner: Before handling na: 336 samples, 1724 features
2019-07-15 15:59:11 WARNING  DataCleaner: Mismatched columns found in dataframe used for fitting and argument dataframe.
2019-07-15 15:59:11 WARNING  DataCleaner: Coercing mismatched columns...
2019-07-15

PymatgenData std_dev atomic_radius  \
filepath                                         
mp-14794                              0.761046   
mp-1185942                            0.353553   
mp-1016846                            0.576318   
mp-757308                             0.635141   
mp-560132                             0.727607   
mp-1173962                            0.527509   
mp-1003638                            0.591163   
mp-1048325                            0.760182   
mp-24939                              0.657267   
mp-555478                             0.680146   
mp-772680                             0.503078   
mp-6641                               0.862510   
mp-1096899                            0.530330   
mp-555268                             0.863252   
mp-1222686                            0.472263   
mp-567026                             0.695475   
mp-1209694                            0.457269   
mp-1174217                            0.516024   
mp-12322                              0.595819   
mp-1177195                            0.565190   
mp-763042                             0.500327   
mp-1213304                            0.889959   
mp-722378                             0.502032   
mp-765737                             0.469255   
mp-772326                             0.428754   
mp-1204153                            0.586965   
mp-1222720                            0.454365   
mp-768003                             0.611414   
mp-647476                             0.637053   
mp-767242                             0.436069   
...                                        ...   
mp-540688                             0.743183   
mp-1177438                            0.504364   
mp-769914                             0.516364   
mp-867312                             0.557524   
mp-1191507                            0.468885   
mp-1204426                            0.657694   
mp-1214308                            0.519482   
mp-15795                              0.314643   
mp-773213                             0.465484   
mp-776511                             0.496991   
mp-29136                              0.743384   
mp-1198264                            0.310934   
mp-756724                             0.673030   
mp-975505                             0.632749   
mp-779804                             0.450185   
mp-24925                              0.530294   
mp-9084                               0.839047   
mp-1191611                            0.397876   
mp-1181872                            0.397777   
mp-36903                              0.848949   
mp-540481                             0.457114   
mp-1178043                            0.521244   
mp-780140                             0.505943   
mp-1227591                            0.360283   
mp-1200356                            0.299235   
mp-1193969                            0.493131   
mp-1047895                            0.601041   
mp-757404                             0.427553   
mp-5504                               0.816788   
mp-1043735                            0.416094   

            PymatgenData std_dev mendeleev_no  \
filepath                                        
mp-14794                            52.920584   
mp-1185942                          14.849242   
mp-1016846                          26.864741   
mp-757308                           44.911260   
mp-560132                           41.209650   
mp-1173962                          49.096515   
mp-1003638                          34.601871   
mp-1048325                          43.595698   
mp-24939                            46.797436   
mp-555478                           36.972073   
mp-772680                           42.664801   
mp-6641                             49.345719   
mp-1096899                          30.405592   
mp-555268                           49.364685   
mp-1222686                          32.607954   
mp-567026                   

In [12]:
masterdf.rename(index=str, columns={'filepath': 'material_id'})

PymatgenData std_dev atomic_radius  \
filepath                                         
mp-14794                              0.761046   
mp-1185942                            0.353553   
mp-1016846                            0.576318   
mp-757308                             0.635141   
mp-560132                             0.727607   
mp-1173962                            0.527509   
mp-1003638                            0.591163   
mp-1048325                            0.760182   
mp-24939                              0.657267   
mp-555478                             0.680146   
mp-772680                             0.503078   
mp-6641                               0.862510   
mp-1096899                            0.530330   
mp-555268                             0.863252   
mp-1222686                            0.472263   
mp-567026                             0.695475   
mp-1209694                            0.457269   
mp-1174217                            0.516024   
mp-12322                              0.595819   
mp-1177195                            0.565190   
mp-763042                             0.500327   
mp-1213304                            0.889959   
mp-722378                             0.502032   
mp-765737                             0.469255   
mp-772326                             0.428754   
mp-1204153                            0.586965   
mp-1222720                            0.454365   
mp-768003                             0.611414   
mp-647476                             0.637053   
mp-767242                             0.436069   
...                                        ...   
mp-540688                             0.743183   
mp-1177438                            0.504364   
mp-769914                             0.516364   
mp-867312                             0.557524   
mp-1191507                            0.468885   
mp-1204426                            0.657694   
mp-1214308                            0.519482   
mp-15795                              0.314643   
mp-773213                             0.465484   
mp-776511                             0.496991   
mp-29136                              0.743384   
mp-1198264                            0.310934   
mp-756724                             0.673030   
mp-975505                             0.632749   
mp-779804                             0.450185   
mp-24925                              0.530294   
mp-9084                               0.839047   
mp-1191611                            0.397876   
mp-1181872                            0.397777   
mp-36903                              0.848949   
mp-540481                             0.457114   
mp-1178043                            0.521244   
mp-780140                             0.505943   
mp-1227591                            0.360283   
mp-1200356                            0.299235   
mp-1193969                            0.493131   
mp-1047895                            0.601041   
mp-757404                             0.427553   
mp-5504                               0.816788   
mp-1043735                            0.416094   

            PymatgenData std_dev mendeleev_no  \
filepath                                        
mp-14794                            52.920584   
mp-1185942                          14.849242   
mp-1016846                          26.864741   
mp-757308                           44.911260   
mp-560132                           41.209650   
mp-1173962                          49.096515   
mp-1003638                          34.601871   
mp-1048325                          43.595698   
mp-24939                            46.797436   
mp-555478                           36.972073   
mp-772680                           42.664801   
mp-6641                             49.345719   
mp-1096899                          30.405592   
mp-555268                           49.364685   
mp-1222686                          32.607954   
mp-567026                   

In [13]:
masterdf.sort_values(by=['probability'], ascending=False)

PymatgenData std_dev atomic_radius  \
filepath                                         
mp-504795                             0.626273   
mvc-6872                              0.632456   
mp-1216961                            0.258349   
mp-1199049                            0.647609   
mp-1217432                            0.225683   
mp-1100966                            0.275810   
mp-685874                             0.275810   
mp-1192730                            0.275810   
mp-1207598                            0.361284   
mp-1213643                            0.570909   
mp-1048853                            0.632456   
mp-1041946                            0.632456   
mvc-6160                              0.632456   
mvc-13150                             0.632456   
mvc-12043                             0.632456   
mp-25690                              0.632456   
mp-1042170                            0.632456   
mp-1041171                            0.632456   
mp-1042970                            0.632456   
mp-1041330                            0.632456   
mvc-2603                              0.572230   
mp-1104185                            0.339633   
mp-764069                             0.567742   
mp-19193                              0.612905   
mp-1216969                            0.226435   
mp-677069                             0.321605   
mp-1216912                            0.301926   
mp-1216835                            0.301926   
mp-1101027                            0.321605   
mp-685403                             0.321605   
...                                        ...   
mp-780641                             0.533333   
mp-769929                             0.533333   
mp-769937                             0.533333   
mp-1692                               0.530330   
mp-14549                              0.530330   
mp-1147768                            0.530330   
mp-1120722                            0.530330   
mp-704645                             0.530330   
mp-1064456                            0.530330   
mp-1178476                            0.530330   
mp-1147673                            0.530330   
mp-1045868                            0.530330   
mp-1478                               0.530330   
mp-772550                             0.565685   
mvc-11548                             0.565685   
mp-779941                             0.565685   
mp-776563                             0.565685   
mp-715566                             0.565685   
mp-779986                             0.565685   
mvc-13134                             0.565685   
mp-510421                             0.565685   
mp-778716                             0.565685   
mvc-13999                             0.565685   
mp-760084                             0.530330   
mp-25229                              0.530330   
mp-510752                             0.530330   
mp-1147761                            0.530330   
mp-510751                             0.530330   
mp-24897                              0.565685   
mp-32905                              0.530330   

            PymatgenData std_dev mendeleev_no  \
filepath                                        
mp-504795                           39.672786   
mvc-6872                            40.421882   
mp-1216961                          26.495941   
mp-1199049                          38.691006   
mp-1217432                          25.084784   
mp-1100966                          25.326440   
mp-685874                           25.326440   
mp-1192730                          25.326440   
mp-1207598                          29.178218   
mp-1213643                          38.214853   
mp-1048853                          40.421882   
mp-1041946                          40.421882   
mvc-6160                            40.421882   
mvc-13150                           40.421882   
mvc-12043                           40.421882   
mp-25690                    

In [14]:
def grouper(iterable, n, fillvalue=None):
    "Collect data into fixed-length chunks or blocks"
    # grouper('ABCDEFG', 3, 'x') --> ABC DEF Gxx
    args = [iter(iterable)] * n
    return zip_longest(fillvalue=fillvalue, *args)

def get_mp_info():
    data = []
    with open("mp_api_key.txt", 'r') as f:
        key = f.readline().strip()
    mpdr = MPDataRetrieval(api_key=key)
    mpid_groups = [g for g in grouper(masterdf.index, 10000)]
    for group in tqdm(mpid_groups):
        # The last group may have fewer than 200 actual ids,
        # so filter the `None`s out.
        mpid_list = list(filter(None, group))
        entries = mpdr.get_data(criteria={"material_id": {"$in": mpid_list}}, 
                            properties=['material_id', 'pretty_formula', 'formation_energy_per_atom'])
        data.extend(entries)
        print('Container is {} bytes'.format(getsizeof(data)))
    return data
info = pd.DataFrame(get_mp_info(), columns=['material_id', 'pretty_formula', 'formation_energy_per_atom'])

  0%|          | 0/9 [00:00<?, ?it/s]

 11%|█         | 1/9 [00:08<01:09,  8.73s/it]


Container is 81048 bytes


 22%|██▏       | 2/9 [00:16<00:59,  8.51s/it]


Container is 161880 bytes


...


Container is 566280 bytes


 89%|████████▉ | 8/9 [01:04<00:07,  7.98s/it]


Container is 647152 bytes


100%|██████████| 9/9 [01:06<00:00,  5.93s/it]


Container is 647152 bytes


In [15]:
masterdf = info.join(masterdf, on=['material_id'])

In [16]:
masterdf = masterdf.sort_values(by=['probability', 'formation_energy_per_atom'], ascending=False)
masterdf.head()

material_id pretty_formula  formation_energy_per_atom  \
13699   mp-504795      Ca4Fe9O17                  -2.274010   
8985     mvc-6872      Ca(FeO2)2                  -2.226603   
39211  mp-1216961        V9InS12                  -1.324639   
29266  mp-1199049         KV6O11                  -2.488637   
39227  mp-1217432  V20Ga(GeS10)4                  -1.263376   

       PymatgenData std_dev atomic_radius  PymatgenData std_dev mendeleev_no  \
13699                            0.626273                          39.672786   
8985                             0.632456                          40.421882   
39211                            0.258349                          26.495941   
29266                            0.647609                          38.691006   
39227                            0.225683                          25.084784   

       MagpieData avg_dev MendeleevNumber  MagpieData avg_dev Column  \
13699                           22.968889                   4.835556   
8985                            23.510204                   4.897959   
39211                           19.822314                   5.206612   
29266                           22.407407                   5.500000   
39227                           17.429586                   4.582249   

       MagpieData avg_dev Electronegativity  MagpieData mean GSvolume_pa  \
13699                              0.916111                    13.414500   
8985                               0.924082                    13.664286   
39211                              0.463636                    20.490568   
29266                              0.915309                    13.962315   
39227                              0.417515                    21.577731   

       MagpieData avg_dev GSvolume_pa  ...  \
13699                        6.494800  ...   
8985                         6.887347  ...   
39211                        6.120465  ...   
29266                        6.571595  ...   
39227                        5.356149  ...   

       MatscholarElementData mean embedding 161  \
13699                                  0.012653   
8985                                   0.014062   
39211                                  0.000670   
29266                                  0.022683   
39227                                 -0.000081   

       MatscholarElementData mean embedding 178  \
13699                                  0.089697   
8985                                   0.090355   
39211                                 -0.027370   
29266                                  0.056697   
39227                                 -0.020957   

       MatscholarElementData mean embedding 180  \
13699                                 -0.136159   
8985                                  -0.135629   
39211                                 -0.176617   
29266                                 -0.162192   
39227                                 -0.175751   

       MatscholarElementData std_dev embedding 183  \
13699                                     0.031724   
8985                                      0.031562   
39211                                     0.061136   
29266                                     0.029936   
39227                                     0.036325   

       MatscholarElementData std_dev embedding 188  \
13699                                     0.064581   
8985                                      0.063589   
39211                                     0.044640   
29266                                     0.081390   
39227                                     0.042229   

       MatscholarElementData range embedding 192  transition metal fraction  \
13699                                   0.093230                   0.300000   
8985                                    0.093230                   0.285714   
39211                                   0.130972                   0.409091   
29266                                   0.081472                   0.333333   
39227        

In [18]:
masterdf.index = masterdf['material_id']
masterdf = masterdf.drop(columns=['material_id'])
masterdf.to_csv("../data/automatminer_MIT_predictions.csv")

In [25]:
masterdf['probability'].head()

material_id
mp-504795     1.0
mvc-6872      1.0
mp-1216961    1.0
mp-1199049    1.0
mp-1217432    1.0
Name: probability, dtype: float64

In [24]:
masterdf.head(n=100)

pretty_formula  formation_energy_per_atom  \
material_id                                             
mp-504795        Ca4Fe9O17                  -2.274010   
mvc-6872         Ca(FeO2)2                  -2.226603   
mp-1216961         V9InS12                  -1.324639   
mp-1199049          KV6O11                  -2.488637   
mp-1217432   V20Ga(GeS10)4                  -1.263376   
mp-685874         V(MoS2)2                  -0.906363   
mp-1192730        V(MoS2)2                  -1.132669   
mp-1207598          YPd3S4                  -1.208698   
mp-1042970       Ca(FeO2)2                  -2.182229   
mp-1041946       Ca(FeO2)2                  -2.199459   
mvc-6160         Ca(FeO2)2                  -2.222660   
mp-1048853       Ca(FeO2)2                  -2.236013   
mp-1041330       Ca(FeO2)2                  -2.268066   
mp-1041171       Ca(FeO2)2                  -2.288782   
mvc-13150        Ca(FeO2)2                  -2.297415   
mp-1042170       Ca(FeO2)2                  -2.300481   
mp-25690         Ca(FeO2)2                  -2.324379   
mvc-12043        Ca(FeO2)2                  -2.326501   
mvc-2603            CaV5O7                  -2.399389   
mp-1104185      TiTl(VS2)4                  -1.358391   
mp-764069        Na2V13O22                  -2.444285   
mp-1216969    V20Ga2Ge3S40                  -1.278754   
mp-677069       Tl3(V3S4)8                  -0.975800   
mp-685403       Tl3(V3S4)8                  -1.005178   
mp-1101027      Tl3(V3S4)8                  -1.029079   
mp-1216835       Tl(V3S4)4                  -1.340149   
mp-1216912       Tl(V3S4)4                  -1.349861   
mvc-11662        Ca(FeO2)4                  -1.673602   
mvc-12189        Ca(FeO2)4                  -1.865803   
mp-1215982        Yb3Fe3S8                  -1.260918   
...                    ...                        ...   
mp-763338            V3O5F                  -2.587092   
mp-850973            V3O5F                  -2.589045   
mp-763912            V3O5F                  -2.589908   
mp-763986            V3O5F                  -2.591906   
mp-1101184           V3O5F                  -2.594069   
mp-763908            V3O5F                  -2.594131   
mp-763291            V3O5F                  -2.606650   
mp-763350            V3O5F                  -2.607690   
mp-510616          NaV6O11                  -2.454215   
mp-25156           NaV6O11                  -2.455236   
mp-567072          NaV6O11                  -2.472204   
mp-680728      K6Fe24S26Cl                  -0.869377   
mp-1208754       SrV5NiO11                  -2.367578   
mp-764309              VOF                  -2.824668   
mp-1215136     Ca3(Fe3O5)5                  -2.057046   
mp-743862     Ca2YFe4SbO12                  -2.508402   
mp-505775           V13O16                  -1.648399   
mp-705541            V10O9                  -1.887355   
mp-705630           V25O32                  -2.286266   
mp-714906             V2O3                  -1.906987   
mp-553955             V2O3                  -1.949823   
mp-1046039            V5O7                  -2.254612   
mp-1045898           V9O13                  -2.272930   
mp-1043388            V2O3                  -2.295912   
mp-776688             V2O3                  -2.432692   
mp-777698             V2O3                  -2.443813   
mp-776630             V2O3                  -2.464601   
mp-849288             V2O3                  -2.497731   
mp-18937              V2O3                  -2.518960   
mp-25787              V2O3                  -2.530604   

             PymatgenData std_dev atomic_radius  \
material_id                                       
mp-504795                              0.626273   
mvc-6872                               0.632456   
mp-1216961                             0.258349   
mp-1199049                             0.647609   
mp-1217432                             0.225683   
mp-685874                              0.275810   
mp-1192730  

In [ ]:
from sklearn.metrics.classification import f1_score

# A list to hold our mse scores for each test fold
f1s = []

# Calculating mse for each test fold
for predicted in predicted_folds:
    # Save the actual K_VRH Series to y_true.
    y_true = predicted["Label"]
    # Save the predicted K_VRH Series to y_test.
    y_test = predicted["Label predicted"]
    f1 = f1_score(y_true, y_test)
    f1s.append(f1)

print(f1s)
print(np.mean(f1s))